In [1]:
################################## Importações para trabalhar com watson IBM ##################################
import json
from ibm_watson import NaturalLanguageUnderstandingV1
from ibm_cloud_sdk_core.authenticators import IAMAuthenticator
from ibm_watson.natural_language_understanding_v1 import Features, EmotionOptions, SentimentOptions, KeywordsOptions
from ibm_watson import ApiException
# from botocore.client import Config
# import ibm_boto3

################################## Importações ##################################
# import types 
import pandas as pd
import re
import string

################################# Importações Google YouTube API #################################
from googleapiclient.discovery import build
import googleapiclient.discovery
#base de dados:
#https://www.kaggle.com/tanulsingh077/twitter-sentiment-extaction-analysis-eda-and-model/output?select=submission.csv

#teste:
#https://natural-language-understanding-demo.ng.bluemix.net/

In [2]:
################################## Configurações serviço IBM ##################################
#realiza autenticação com servidor IBM
authenticator = IAMAuthenticator('LsRvjTiGO2hm5CmMOkYumONXX1x08ej0nZED2cRZYvqM')
service = NaturalLanguageUnderstandingV1(
    version='2020-08-01',
    authenticator=authenticator
)

# #seleciona o serviço de processamento de linguagem natural
service.set_service_url('https://api.us-south.natural-language-understanding.watson.cloud.ibm.com/instances/fe0885df-7c76-4192-9bc8-6c6d7ca836ae')

In [109]:

################################## INÍCIO FUNÇÕES IBM ##################################
def sentiment_and_emotion(st,service=service):
    """
    Função para fazer requisição com o servidor IBM e obter emoção e sentimento do texto a ser analisado
    return: JSON com análises do texto informado
    """
    try:
        return (service.analyze(text=st,features=Features(emotion=EmotionOptions(),sentiment=SentimentOptions())).get_result())
    except ApiException as ex:
        return "NULL"
    #analisa a emoção do texto contido na variável st
    #return (service.analyze(text=st,features=Features(emotion=EmotionOptions())).get_result())
    

def sentiment_extractor(row_num):
    """
    Função para pegar o score do sentimento e colocar em uma nova coluna dataframe
    return: score do sentimento
    """ 
    #print(row_num)    
    try:
        
        sentiment = filtrado['sentiment_keyword_json'][row_num]['sentiment']['document']['label']
        #print(sentiment)
        return sentiment
    except:
        return "NULL"
################################## FIM FUNÇÕES IBM ##################################

In [120]:
################################## INÍCIO FUNÇÕES LIMPEZA TEXTOS ##################################

def clean_text(text):
    """
    Função para remover caracteres especiais, http...
    """
    # Letras minúsculas
    text = str(text).lower()
    #trim
    text = str(text).strip()

    # Remove nome do usuário
    text = re.sub(r"@[A-Za-z0-9$-_@.&+]+", ' ', text)
    
    # Remove URLs
    text = re.sub(r"https?://[A-Za-z0-9./]+", ' ', text)    
    
    text = re.sub('\[.*?\]', '', text)

    text = re.sub('<.*?>+', '', text)
    text = re.sub('[%s]' % re.escape(string.punctuation), '', text)
    text = re.sub('\n', '', text)
    text = re.sub('\w*\d\w*', '', text)  
    
    return text

def emotion_extractor(row_num):
    """
    Função para pegar o score do sentimento e colocar em uma nova coluna dataframe
    return: score do sentimento
    """    
    #sentiment_scores=df2['sentiment_keyword_json'][row_num]['sentiment']['document']
    #print(filtrado['sentiment_keyword_json'][row_num]['emotion']['document']['emotion'])
    try:
        dictResult = filtrado['sentiment_keyword_json'][row_num]['emotion']['document']['emotion']
        dictResult = [max(dictResult, key=dictResult.get)]
        return dictResult[0]
    except:
        return "NULL"

################################## FIM FUNÇÕES LIMPEZA TEXTOS ##################################

In [5]:
#FIX: COLOCAR CÓDIGO PARA PEGAR COMENTÁRIOS DO YOUTUBE (FAZER COMO FUNÇÃO)
################################## INÍCIO FUNÇÃO PARA LER COMENTÁRIOS YOUTUBE ##################################
#https://www.pingshiuanchua.com/blog/post/using-youtube-api-to-analyse-youtube-comments-on-python
def get_comment_you_api(video_id):
    readApiKey = pd.read_csv('apiYouTubeKey.txt', sep="\t")

    api_key = str(readApiKey[readApiKey['api'] == 'YouTube']['key'][0])
    #youtube = build('youtube','v3', developerKey=youTubeApiKey)

    df_result = pd.DataFrame(columns=['comments'])
    cont = 0

    service = build('youtube', 'v3', developerKey=api_key) 

    response = service.commentThreads().list(
                    part = 'snippet',
                    videoId = video_id,
                    maxResults = 500, 
                    order = 'relevance',
                    textFormat = 'plainText',
                    ).execute()

    for item in response['items']:
        #print(item['snippet']['topLevelComment']['snippet']['textDisplay'])
        #print(item['snippet']['topLevelComment']['snippet']['textOriginal'])
        df_result.loc[cont] = item['snippet']['topLevelComment']['snippet']['textDisplay']
        cont = cont + 1

    return df_result
################################## FIM FUNÇÃO PARA LER COMENTÁRIOS YOUTUBE ##################################

In [96]:
################## get comments from YOUTUBE API ################## 
#set dataframe
df_comments = pd.DataFrame(columns=['comments'])

################################
#old trailer
################################

#get comments from video:
#https://www.youtube.com/watch?v=1ax0Pb7j6Fc
df_comments = get_comment_you_api("1ax0Pb7j6Fc")

#get comments from video:
#https://www.youtube.com/watch?v=-QHKFPD9iRE
df_comments = pd.concat([df_comments, get_comment_you_api("-QHKFPD9iRE")], ignore_index=True)

#get comments from video:
#https://www.youtube.com/watch?v=s4dYb-NTyKA
df_comments = pd.concat([df_comments, get_comment_you_api("s4dYb-NTyKA")], ignore_index=True)

#get comments from video:
#https://www.youtube.com/watch?v=4mW9FE5ILJs
df_comments = pd.concat([df_comments, get_comment_you_api("4mW9FE5ILJs")], ignore_index=True)

#get comments from video:
#https://www.youtube.com/watch?v=BLGY_cWF9lk
df_comments = pd.concat([df_comments, get_comment_you_api("BLGY_cWF9lk")], ignore_index=True)

#Reacts
#get comments from video:
#https://www.youtube.com/watch?v=izjGqvyelMc
df_comments = pd.concat([df_comments, get_comment_you_api("izjGqvyelMc")], ignore_index=True)

#get comments from video:
#https://www.youtube.com/watch?v=JJ56BzdB5vE
df_comments = pd.concat([df_comments, get_comment_you_api("JJ56BzdB5vE")], ignore_index=True)

#get comments from video:
#https://www.youtube.com/watch?v=tZOHtT0IV24
df_comments = pd.concat([df_comments, get_comment_you_api("tZOHtT0IV24")], ignore_index=True)

#get comments from video:
#https://www.youtube.com/watch?v=W3PcYZyhuT4
df_comments = pd.concat([df_comments, get_comment_you_api("W3PcYZyhuT4")], ignore_index=True)

#get comments from video:
#https://www.youtube.com/watch?v=aSlj0OXtads
df_comments = pd.concat([df_comments, get_comment_you_api("aSlj0OXtads")], ignore_index=True)
#print(df_comments['comments'])

In [97]:
#requisição com servidor IBM, para classificar os comentários
#parâmetros:
    #texto
    #eixo para adicionar a coluna
    
#df_comments = df_comments.head()    
df_comments.apply(lambda row : clean_text(str(row['comments'])),axis = 1)

df_comments['sentiment_keyword_json'] = df_comments.apply(lambda row : sentiment_and_emotion(str(row['comments'])),axis = 1)
df_comments

comments  \
0    Oh God, I'm not even a sonic fan and this look...   
1    Here before the "Who came here after the new t...   
2                   Look at how they massacred my boy.   
3                       1:11 internet reaction to this   
4    I start to think we live in the wrong universe...   
..                                                 ...   
995  It looks like a CGI sonic, I don’t get why eve...   
996  It’s his eyes his eyes make the entire design ...   
997    I've never fast forwarded so much ina video....   
998  Can’t believe this movie come out on my birthd...   
999  lmao Sam's reaction to seeing Sonic's face.......   

                                sentiment_keyword_json  
0    {'usage': {'text_units': 1, 'text_characters':...  
1    {'usage': {'text_units': 1, 'text_characters':...  
2    {'usage': {'text_units': 1, 'text_characters':...  
3    {'usage': {'text_units': 1, 'text_characters':...  
4    {'usage': {'text_units': 1, 'text_characters':...  
..                                                 ...  
995  {'usage': {'text_units': 1, 'text_characters':...  
996  {'usage': {'text_units': 1, 'text_characters':...  
997  {'usage': {'text_units': 1, 'text_characters':...  
998  {'usage': {'text_units': 1, 'text_characters':...  
999  {'usage': {'text_units': 1, 'text_characters':...  

[1000 rows x 2 columns]

In [128]:
#obter somente o label
#df_comments.to_csv("database/testeDadosClassificados.csv", encoding='utf-8', index=False)

#df_data_1 = pd.read_csv('database/testeDadosClassificados.csv')

filtrado = df_comments[df_comments['sentiment_keyword_json'] != 'NULL']
filtrado.dropna(inplace=True)
filtrado = filtrado.reset_index()
filtrado = filtrado.drop(columns=['index'])

filtrado['sentiment'] = filtrado.apply(lambda row : sentiment_extractor(row.name),axis = 1)
filtrado['emotion'] = filtrado.apply(lambda row : emotion_extractor(row.name),axis = 1)


filtrado.to_csv("database/trailerOldSentimentEmotion.csv", encoding='utf-8', index=False)

filtrado.shape

<ipython-input-128-12e5eaf9512d>:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtrado.dropna(inplace=True)


(977, 4)

In [125]:
filtrado

comments  \
0    Oh God, I'm not even a sonic fan and this look...   
1    Here before the "Who came here after the new t...   
2                   Look at how they massacred my boy.   
3                       1:11 internet reaction to this   
4    I start to think we live in the wrong universe...   
..                                                 ...   
972  It looks like a CGI sonic, I don’t get why eve...   
973  It’s his eyes his eyes make the entire design ...   
974    I've never fast forwarded so much ina video....   
975  Can’t believe this movie come out on my birthd...   
976  lmao Sam's reaction to seeing Sonic's face.......   

                                sentiment_keyword_json sentiment  emotion  
0    {'usage': {'text_units': 1, 'text_characters':...  negative  sadness  
1    {'usage': {'text_units': 1, 'text_characters':...  negative     fear  
2    {'usage': {'text_units': 1, 'text_characters':...  negative  disgust  
3    {'usage': {'text_units': 1, 'text_characters':...   neutral    anger  
4    {'usage': {'text_units': 1, 'text_characters':...   neutral      joy  
..                                                 ...       ...      ...  
972  {'usage': {'text_units': 1, 'text_characters':...  negative  sadness  
973  {'usage': {'text_units': 1, 'text_characters':...  negative      joy  
974  {'usage': {'text_units': 1, 'text_characters':...  negative      joy  
975  {'usage': {'text_units': 1, 'text_characters':...  negative      joy  
976  {'usage': {'text_units': 1, 'text_characters':...  negative      joy  

[977 rows x 4 columns]

In [182]:
#####salvando dados classificados em csv
saveFile = filtrado.drop(columns=['sentiment_emotion_json'])
saveFile.to_csv("database/testeDadosClassificados.csv", encoding='utf-8', index=False)

In [2]:
readFile = pd.read_csv('database/testeDadosClassificados.csv')

In [3]:
readFile

selected_text sentiment  emotion
0                           last session of the day     neutral  sadness
1                                            exciting  positive      joy
2                                          happy bday  positive      joy
3   and within a short time of the last clue all o...  negative  sadness
4   what did you get  my day is alright havent don...  negative  sadness
5   my bike was put on holdshould have known that ...  negative     fear
6                             i checked  we didnt win  negative      joy
7    and youre on twitter did the tavern bore you ...  negative  sadness
8   i feel like my phones hole is not a virgin tha...  negative  sadness
9   im going into a spiritual stagnentation its ex...  positive      joy
10  my dead grandpa pays more attention to me than...  negative  sadness
11                               about to go to sleep   neutral     fear
12                                      thats so cool  positive      joy
13  hey peoples dont you just hate being grounded ...  negative  sadness
14               huh another scarepoint coding sunday   neutral      joy
15                  look who i found just for you      positive      joy
16  no ac the fan doesnt swing our way  we are swe...  negative      joy

Oh God, I'm not even a sonic fan and this looks terrible.
Here before the "Who came here after the new trailer" storm.
Look at how they massacred my boy.
1:11 internet reaction to this
I start to think we live in the wrong universe where this is allowed to exist.
Detective Pikachu would be better than this Sonic film as the trailer would be a first kid cartoon, based on the manga, to get good reviews.
They had to be snorting ALL the coke when they greenlit this ungodly travesty.
0:54 is he about to say the n word
Therapist: Old design Sonic doesn't exist he can't hurt you.
Old Design Sonic: 0:27
As the world's political and ecological climates teeter on the brink of collapse, the Sonic the Hedgehog trailer is a subtle but powerful reminder that God will not protect us.
Paramount: let's delete this trailer from the internet
Columbia: *N O*
just passing by after watching the redesigned new Sonic Trailer
RIP Sonic old design I hope you don't go to heaven
Why ive gotten this as a commercia

Jim carry is back
welp i still loving this trailer
change the music for the next teaser trailer


Comment by Sharleen Butler: 𝗡𝗼𝘄 𝗢𝗻 𝗧𝗿𝗲𝗻𝗱𝗶𝗻𝗴🔥
hotslut.live/xxx323amateurvideodate
⬇️⬇️⬇️⬇️⬇️⬇️⬇️



!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。 說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木 來調味食物煮的時候!!
Comment by Wendy Lloyd: 𝘾𝙡𝙞𝙘𝙠𝙃𝙚𝙧𝙚⏩ hotslut.live/horny691hentaixxx

在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候//
Comment by Elaine Maxwell: hotslut.live/795xxxamateurvideogirlsuck
   》》 𝙊𝙣𝙡𝙮 𝘼𝙙𝙪𝙡𝙩 《《


!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候^^

Comment by Sharleen Butler: 𝗡𝗼𝘄 𝗢𝗻 𝗧𝗿𝗲𝗻𝗱𝗶𝗻𝗴🔥
hotslut.live/xxx323amateurvideodate
⬇️⬇️⬇️⬇️⬇️⬇️⬇️



!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。 說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木 來調味食物煮的時候!!
Comment by Wendy Lloyd: 𝘾𝙡𝙞𝙘𝙠𝙃𝙚𝙧𝙚⏩ hotslut.live/horny691hentaixxx

在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候//
Comment by Elaine Maxwell: hotslut.live/795xxxamateurvideogirlsuck
   》》 𝙊𝙣𝙡𝙮 𝘼𝙙𝙪𝙡𝙩 《《


!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候^^

Comment by Sharleen Butler: 𝗡𝗼𝘄 𝗢𝗻 𝗧𝗿𝗲𝗻𝗱𝗶𝗻𝗴🔥
hotslut.live/xxx323amateurvideodate
⬇️⬇️⬇️⬇️⬇️⬇️⬇️



!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。 說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木 來調味食物煮的時候!!
Comment by Wendy Lloyd: 𝘾𝙡𝙞𝙘𝙠𝙃𝙚𝙧𝙚⏩ hotslut.live/horny691hentaixxx

在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候//
Comment by Elaine Maxwell: hotslut.live/795xxxamateurvideogirlsuck
   》》 𝙊𝙣𝙡𝙮 𝘼𝙙𝙪𝙡𝙩 《《


!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候^^

Comment by Sharleen Butler: 𝗡𝗼𝘄 𝗢𝗻 𝗧𝗿𝗲𝗻𝗱𝗶𝗻𝗴🔥
hotslut.live/xxx323amateurvideodate
⬇️⬇️⬇️⬇️⬇️⬇️⬇️



!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。 說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木 來調味食物煮的時候!!
Comment by Wendy Lloyd: 𝘾𝙡𝙞𝙘𝙠𝙃𝙚𝙧𝙚⏩ hotslut.live/horny691hentaixxx

在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候//
Comment by Elaine Maxwell: hotslut.live/795xxxamateurvideogirlsuck
   》》 𝙊𝙣𝙡𝙮 𝘼𝙙𝙪𝙡𝙩 《《


!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候^^

Comment by Sharleen Butler: 𝗡𝗼𝘄 𝗢𝗻 𝗧𝗿𝗲𝗻𝗱𝗶𝗻𝗴🔥
hotslut.live/xxx323amateurvideodate
⬇️⬇️⬇️⬇️⬇️⬇️⬇️



!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。 說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木 來調味食物煮的時候!!
Comment by Wendy Lloyd: 𝘾𝙡𝙞𝙘𝙠𝙃𝙚𝙧𝙚⏩ hotslut.live/horny691hentaixxx

在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候//
Comment by Elaine Maxwell: hotslut.live/795xxxamateurvideogirlsuck
   》》 𝙊𝙣𝙡𝙮 𝘼𝙙𝙪𝙡𝙩 《《


!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候^^

...

Comment by Sharleen Butler: 𝗡𝗼𝘄 𝗢𝗻 𝗧𝗿𝗲𝗻𝗱𝗶𝗻𝗴🔥
hotslut.live/xxx323amateurvideodate
⬇️⬇️⬇️⬇️⬇️⬇️⬇️



!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。 說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木 來調味食物煮的時候!!
Comment by Wendy Lloyd: 𝘾𝙡𝙞𝙘𝙠𝙃𝙚𝙧𝙚⏩ hotslut.live/horny691hentaixxx

在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候//
Comment by Elaine Maxwell: hotslut.live/795xxxamateurvideogirlsuck
   》》 𝙊𝙣𝙡𝙮 𝘼𝙙𝙪𝙡𝙩 《《


!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候^^

Comment by Sharleen Butler: 𝗡𝗼𝘄 𝗢𝗻 𝗧𝗿𝗲𝗻𝗱𝗶𝗻𝗴🔥
hotslut.live/xxx323amateurvideodate
⬇️⬇️⬇️⬇️⬇️⬇️⬇️



!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。 說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木 來調味食物煮的時候!!
Comment by Wendy Lloyd: 𝘾𝙡𝙞𝙘𝙠𝙃𝙚𝙧𝙚⏩ hotslut.live/horny691hentaixxx

在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候//
Comment by Elaine Maxwell: hotslut.live/795xxxamateurvideogirlsuck
   》》 𝙊𝙣𝙡𝙮 𝘼𝙙𝙪𝙡𝙩 《《


!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候^^

Comment by Sharleen Butler: 𝗡𝗼𝘄 𝗢𝗻 𝗧𝗿𝗲𝗻𝗱𝗶𝗻𝗴🔥
hotslut.live/xxx323amateurvideodate
⬇️⬇️⬇️⬇️⬇️⬇️⬇️



!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。 說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木 來調味食物煮的時候!!
Comment by Wendy Lloyd: 𝘾𝙡𝙞𝙘𝙠𝙃𝙚𝙧𝙚⏩ hotslut.live/horny691hentaixxx

在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候//
Comment by Elaine Maxwell: hotslut.live/795xxxamateurvideogirlsuck
   》》 𝙊𝙣𝙡𝙮 𝘼𝙙𝙪𝙡𝙩 《《


!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候^^

Comment by Sharleen Butler: 𝗡𝗼𝘄 𝗢𝗻 𝗧𝗿𝗲𝗻𝗱𝗶𝗻𝗴🔥
hotslut.live/xxx323amateurvideodate
⬇️⬇️⬇️⬇️⬇️⬇️⬇️



!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。 說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木 來調味食物煮的時候!!
Comment by Wendy Lloyd: 𝘾𝙡𝙞𝙘𝙠𝙃𝙚𝙧𝙚⏩ hotslut.live/horny691hentaixxx

在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候//
Comment by Elaine Maxwell: hotslut.live/795xxxamateurvideogirlsuck
   》》 𝙊𝙣𝙡𝙮 𝘼𝙙𝙪𝙡𝙩 《《


!❤️ 在整個人類歷史上，強者，富人和具有狡猾特質的人捕食部落，氏族，城鎮，城市和鄉村中的弱者，無`'守和貧窮成員。然而，人類的生存意願迫使那些被拒絕，被剝奪或摧毀的基本需求的人們找到了一種生活方式，並繼續將其DNA融入不斷發展的人類社會。
說到食物，不要以為那些被拒絕的人只吃垃圾。相反，他們學會了在被忽視的肉類和蔬菜中尋找營養。他們學會了清潔，切塊，調味和慢燉慢燉的野菜和肉類，在食品市場上被忽略的部分家用蔬菜和肉類，並且學會了使用芳香的木煙（如山核桃，山核桃和豆科灌木
來調味食物煮的時候^^

KeyboardInterrupt: 

In [ ]:
api_key = str(readApiKey[readApiKey['api'] == 'YouTube']['key'][0])
#youtube = build('youtube','v3', developerKey=youTubeApiKey)
video_id = "1ax0Pb7j6Fc"